<a href="https://colab.research.google.com/github/qubit55/ml-tutorials/blob/main/time_series_forecasting_tutorial_clojure.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

# Time Series Forecasting using Clojure

Time series forecasting, is a task of predicting future values based on historical data. It plays a crucial role in various domains such as finance, economics, weather forecasting, etc. In this notebook, I'm going to show you how to use Clojure and its ML tools to perform time series forecasting tasks, specifically forecasting half-hourly electricity demand in England and Wales using the 'taylor' dataset from the 'forecast' R package. I hope this can be a good starting point for anyone who wants to use Clojure for data science and machine learning.

## First, install Clojupyter kernel

Google Colab doesn't include a Clojure Jupyter kernel by default, we'll need to install it manually. The [install_clojure_kernel.sh](https://github.com/qubit55/clojupyter_colab_setup/blob/main/install_clojure_kernel.sh) script will handle all the necessary steps. Just run the cell below, and the Clojure kernel will be ready to use.

After the installation process has finished, change the runtime to Clojure IPC and wait for the Clojupyter kernel to connect.

In [ ]:
# Install Clojupyter kernel
!wget https://raw.githubusercontent.com/qubit55/clojupyter_colab_setup/refs/heads/main/install_clojure_kernel.sh
!chmod +x install_clojure_kernel.sh
!./install_clojure_kernel.sh

Syntax error reading source at (REPL:1:21).
No reader function for tag Install


class clojure.lang.ExceptionInfo: 

## External dependencies

Now we need to add all the libraries we're going to use in this notebook. We're going use quite a bit of them, so I will quickly mention only the most prominent ones:
*   **`tablecloth`**: For easy data manipulation and transformation, similar to dplyr in R and Pandas in Python. It's going to be our go-to for loading, cleaning, and manipulating data in a tabular format.
*   **`hanami`**: This library is useful for creating data visualizations. It uses a declarative approach based on the Vega-Lite grammar, making it easy to create interactive charts and graphs.
*   **`scicloj.ml`**: Provides a comprehensive collection of algorithms and tools for training models, evaluating their performance, and making predictions.
*   **`clojure.java-time`**: Dealing with dates and times.
*   **`tableplot`**: This library acts as a bridge between Tablecloth and Hanami.

In [ ]:
(require '[clojupyter.misc.helper :as helper]
         '[clojupyter.display :as display])

nil

In [ ]:
(helper/add-dependencies '[org.scicloj/tableplot "1-beta10.2"])
(helper/add-dependencies '[org.scicloj/metamorph.ml "1.1.1"])
(helper/add-dependencies '[org.scicloj/scicloj.ml.smile "7.5.0"])
(helper/add-dependencies '[scicloj/tablecloth "7.029.2"])
(helper/add-dependencies '[org.scicloj/tablecloth.time "1.00-alpha-5"])
(helper/add-dependencies '[aerial.hanami "0.15.1"])
(helper/add-dependencies '[clojure.java-time "1.4.3"])
(helper/add-dependencies '[metosin/jsonista "0.3.13"])
(helper/add-dependencies '[generateme/fastmath "3.0.0-alpha3"])

org.apache.commons/commons-math3 3.6.1 jfree/jfreechart 1.0.12 :scope runtime jfree/jcommon 1.0.15 :scope runtime pl.edu.icm/JLargeArrays 1.5 org.clojure/data.int-map 1.3.0 com.github.wendykierp/JTransforms 3.1 pl.edu.icm/JLargeArrays 1.5 jfree/jcommon 1.0.15 :scope runtime colt 1.2.0 :scope runtime concurrent 1.3.4 :scope runtime com.github.rwl/optimization 1.3 :scope runtime de.sciss/jwave 1.0.3 org.clojure/clojure 1.9.0 org.clojure/core.specs.alpha 0.1.24 org.clojure/spec.alpha 0.1.143 generateme/fastmath 3.0.0-alpha3 org.apache.commons/commons-math3 3.6.1 org.clojure/data.int-map 1.3.0 com.github.wendykierp/JTransforms 3.1 de.sciss/jwave 1.0.3 net.jafama/jafama 2.3.2 ca.umontreal.iro.simul/ssj 3.3.1 org.clojure/math.combinatorics 0.3.0 org.clojure/core.specs.alpha 0.1.24 concurrent 1.3.4 :scope runtime net.jafama/jafama 2.3.2 ca.umontreal.iro.simul/ssj 3.3.1 jfree/jfreechart 1.0.12 :scope runtime colt 1.2.0 :scope runtime com.github.rwl/optimization 1.3 :scope runtime org.clojure/math.combinatorics 0.3.0 org.clojure/clojure 1.9.0 org.clojure/spec.alpha 0.1.143

In [ ]:
(require '[tablecloth.api :as tc]
         '[clojure.string :as str]
         '[scicloj.tableplot.v1.hanami :as hanami]
         '[tech.v3.datatype.datetime :as datetime]
         '[tech.v3.dataset.metamorph :as ds-mm]
         '[aerial.hanami.templates :as ht]
         '[aerial.hanami.common :as hc]
         '[scicloj.metamorph.ml :as ml]
         '[scicloj.metamorph.ml.loss :as loss]
         '[scicloj.metamorph.core :as mc]
         '[scicloj.metamorph.ml.preprocessing :as mm-preprop]
         '[tablecloth.pipeline :as tc-mm]
         '[scicloj.ml.smile.regression]
         '[java-time.api :as jtime]
         '[jsonista.core :as j]
         '[fastmath.random :as r])

Register model:  :smile.regression/ordinary-least-square
Register model:  :smile.regression/elastic-net
Register model:  :smile.regression/lasso
Register model:  :smile.regression/ridge
Register model:  :smile.regression/gradient-tree-boost
Register model:  :smile.regression/random-forest


nil

## Define some helpers

Here we're going to define some helper functions to display Vega lite graphics and fetch R datasets.

In [ ]:
(defn show
  [vega-lite-spec]
  ;; Need to manually embed Vega-Lite spec so Colab can display it
  (let [json-spec (j/write-value-as-string vega-lite-spec)]
    (display/hiccup-html
      [:html
       [:head
        [:title "Embedding Vega-Lite"]
        [:script {:src "https://cdn.jsdelivr.net/npm/vega@5.30.0"}]
        [:script {:src "https://cdn.jsdelivr.net/npm/vega-lite@5.21.0"}]
        [:script {:src "https://cdn.jsdelivr.net/npm/vega-embed@6.26.0"}]]
       [:body
        [:div {:id "vis"}]
        [:script {:type "text/javascript"}
         (str "var yourVlSpec = " json-spec ";
               vegaEmbed('#vis', yourVlSpec);")]]])))

#'user/show

In [ ]:
(defn fetch-dataset [dataset-name]
  "To fetch R datasets"
  (-> dataset-name
      (->> (format "https://vincentarelbundock.github.io/Rdatasets/csv/%s.csv"))
      (tc/dataset {:key-fn (fn [k]
                             (-> k
                                 str/lower-case
                                 (str/replace #"\." "-")
                                 keyword))})
      (tc/set-dataset-name dataset-name)))

#'user/fetch-dataset

## Load the data

This section loads the 'taylor' dataset, which contains half-hourly electricity demand data for England and Wales from Monday 5 June 2000 to Sunday 27 August 2000. The demand is measured in Megawatts.

In [ ]:
(defonce data-raw (fetch-dataset "forecast/taylor"))
;; Description https://www.rdocumentation.org/packages/forecast/versions/8.23.0/topics/taylor

#'user/data-raw

Let's check the first 5 observations.

In [ ]:
(tc/head data-raw 5)

forecast/taylor [5 2]: :rownames :x 1 22262 2 21756 3 22247 4 22759 5 22549

As can be seen above, there's no timestamp attached to the data, so let's generate it and attach to the data.

Remember that the step is half an hour.

In [ ]:
(defn half-hourly-intervals
  [start-dt end-dt]
  (->> (iterate #(jtime/plus % (jtime/minutes 30)) start-dt)
       (take-while (fn [dt] (not (jtime/after? dt end-dt))))))

#'user/half-hourly-intervals

In [ ]:
(def start (jtime/local-date-time 2000 6 5 0 0)) ;; 5 June 2000 12:00 am
(def end   (jtime/local-date-time 2000 8 27 23 30)) ;; 27 August 2000 11:30 pm

#'user/end

In [ ]:
(def datetime-grid (half-hourly-intervals start end))

#'user/datetime-grid

In [ ]:
(take 3 datetime-grid)

2000-06-05T00:00 2000-06-05T00:30 2000-06-05T01:00

In [ ]:
(def ts-data
 (-> data-raw
  (tc/add-column :datetime datetime-grid)
  (tc/rename-columns {:x :demand-mw})))

#'user/ts-data

In [ ]:
(tc/head ts-data 3)

forecast/taylor [3 3]: :rownames :demand-mw :datetime 1 22262 2000-06-05T00:00 2 21756 2000-06-05T00:30 3 22247 2000-06-05T01:00

## Visualize the data

Alright, we've got our data loaded and ready to go. Now, let's see what it actually looks like! I'm going to use Hanami and its templates for this. I'll also add a LOESS (https://en.wikipedia.org/wiki/Local_regression) smoother, which basically helps us see the average trend in the data more clearly.

In [ ]:
(-> ts-data
  (hanami/plot ht/layer-chart
     {:LAYER [(hanami/plot ht/line-chart
                {:X "rownames"
                 :XTYPE "quantitative"
                 :Y "demand-mw"
                 :YTYPE "quantitative"
                 :TRANSFORM [{:loess :demand-mw :on :rownames}]
                 :MCOLOR "red"
                 :MSIZE 3
                 :WIDTH 1000
                 :HEIGHT 300})
             (hanami/plot ht/line-chart
                {:X "rownames"
                 :XTYPE "quantitative"
                 :Y "demand-mw"
                 :YTYPE "quantitative"})
             (hanami/plot ht/point-chart
                {:X "rownames"
                 :XTYPE "quantitative"
                 :Y "demand-mw"
                 :YTYPE "quantitative"})]})
  (show))

Embedding Vega-Lite

The average trend appears to be stationary, meaning it neither increases nor decreases over time. In other words, the mean of the time series remains constant and does not depend on time. In time series literature, this is referred to as first-order stationarity. This suggests that electricity demand in England and Wales during the observed period is relatively stable. This is an important observation for forecasting, as it allows the use of simpler models that do not need to account for long-term trends. However, the data clearly exhibits seasonality, which will still need to be modeled appropriately.

Before we move forward, it's good practice to set aside a portion of the data as a test set to evaluate the final performance of the model. The test set provides a less biased estimate of how the model might perform in real-world scenarios. That said, it doesn't eliminate all bias, and there are still limitations to what it can tell us.

Let's set the forecast horizon to 7 days. We'll split the data into a training set from 5 June 2000 to 19 August 2000, and a test set from 20 August 2000 to the end (27 August 2000). The test set should be the same length as our forecast horizon to get a less biased estimate of the model's performance.

In [ ]:
;; Let's find the latest datetime
(def latest-datetime
 (-> ts-data
  (tc/order-by :datetime :desc)
  :datetime
  first))

latest-datetime

2000-08-27T23:30

In [ ]:
(def forecast-horizon 7) ;; in days

#'user/forecast-horizon

In [ ]:
(def cutoff
 (jtime/minus latest-datetime (jtime/days forecast-horizon)))
cutoff

2000-08-20T23:30

Now, instead of literally splitting the data into two parts, let's add an indicator variable to label whether each chunk belongs to the training or test set. This will greatly simplify data visualization, especially when we need both chunks to appear on the same plot.

In [ ]:
(def ts-data-split
 (-> ts-data
  (tc/add-column
  :is-train (fn [ds] (map (fn [x] (case (jtime/before? x cutoff) true 1 false 0)) (:datetime ds))))))

#'user/ts-data-split

The plot below displays the training set in orange, and the test set in blue. Everything looks pretty good.

In [ ]:
(-> ts-data-split
    (hanami/base {:=x :datetime
                  :=y :demand-mw})
    (hanami/layer-line {:=color "is-train"})
    (hanami/layer-point {:=color "is-train"})
    (assoc :background "lightgrey"
           :width 800
           :height 300)
    (hanami/plot)
    show)

Embedding Vega-Lite

Now, in order to make it easy to train our model, eventually, we need to actually separate the training and test sets by filtering them out from the original dataset.

In [ ]:
(def train-df
 (tc/select-rows ts-data-split
  (comp #(= 1 %) :is-train)))

#'user/train-df

In [ ]:
(tc/shape train-df)

3695 4

In [ ]:
(def test-df
 (tc/select-rows ts-data-split
  (comp #(= 0 %) :is-train)))

#'user/test-df

In [ ]:
(tc/shape test-df)

337 4

We have 3695 observations in the training set and 337 in the test sets.

## Feature Engineering

Every machine learning model requires a set of features (also known as predictors, covariates, or independent variables). So, let's create some features from our dataset.

As we've already seen, the data exhibits seasonality. What could explain this seasonal behavior? A few ideas that come to mind include:

- Time of day  
- Day of the week  
- Whether it's morning or evening  
- Whether it's a weekend  

These kinds of temporal features often capture regular patterns in electricity demand.

I’ve previously mentioned that we don’t need to explicitly model the trend (since the data appears stationary in the mean), but for completeness, I’ll still show how to extract a trend-like feature to demonstrate how it can be derived and normalized for use in a model. So, let's define a couple of functions to help with that.

In [ ]:
(defn ms-since-epoch [dt]
  (.toEpochMilli
    (jtime/instant
      (.atZone dt (jtime/zone-id "Europe/London")))))

#'user/ms-since-epoch

In [ ]:
(defn stage-expand-time-features
 [df datetime-col]
 (-> df
  (tc/map-columns :month [datetime-col] jtime/month)
  (tc/map-columns :day-of-week [datetime-col] jtime/day-of-week)
  (tc/map-columns :minute-of-day [datetime-col] #(+ (* 60.0 (.getHour %)) (.getMinute %)))
  (tc/map-columns :weekend [datetime-col] #(case (jtime/weekend? %) true 1 false 0))
  (tc/map-columns :am [datetime-col] #(if (< (.getHour %) 12) 1 0))
  (tc/map-columns :day-of-month [datetime-col] #(.getDayOfMonth %) )
  (tc/map-columns :epoch-ms [datetime-col] #(ms-since-epoch %))))

#'user/stage-expand-time-features

##  What Each Feature Does

- `:month` — Numeric month (1–12)
- `:day-of-week` — Day of the week (e.g., Monday = 1)
- `:minute-of-day` — Minutes since midnight (0–1439), useful to capture fine-grained time cycles
- `:weekend` — `1` if Saturday/Sunday, `0` otherwise
- `:am` — `1` for morning (before noon), `0` otherwise
- `:day-of-month` — Day within the month
- `:epoch-ms` — Milliseconds since the Unix epoch — can be useful as a proxy for trend, especially after normalization


To apply the time-based feature engineering to our training set, we simply pass the dataset through the stage-expand-time-features function, specifying the :datetime column. To keep things tidy and verify the output, we'll just preview the first few rows:

In [ ]:
(-> train-df
  (stage-expand-time-features :datetime)
  (tc/head 5))

forecast/taylor [5 11]: :rownames :demand-mw :datetime :is-train :month :day-of-week :minute-of-day :weekend :am :day-of-month :epoch-ms 1 22262 2000-06-05T00:00 1 JUNE MONDAY 0.0 0 1 5 960159600000 2 21756 2000-06-05T00:30 1 JUNE MONDAY 30.0 0 1 5 960161400000 3 22247 2000-06-05T01:00 1 JUNE MONDAY 60.0 0 1 5 960163200000 4 22759 2000-06-05T01:30 1 JUNE MONDAY 90.0 0 1 5 960165000000 5 22549 2000-06-05T02:00 1 JUNE MONDAY 120.0 0 1 5 960166800000

## Exploring Feature Relationships with Demand

Now that we’ve created a set of time-based features, it’s a good idea to explore how they relate to our target variable, `:demand-mw`. This step helps us evaluate whether these features carry useful signals that the model can learn from. If we notice clear patterns or relationships (e.g., demand tends to spike on weekdays or drops at night), that’s a strong hint that the feature could improve forecast accuracy.

To do this, we’ll reshape our data into a long (tidy) format, which makes it easier to visualize the relationship between each feature and the target variable on a single plot using Vega-Lite. The tidy format is a common structure for organizing data where each variable is a column, each observation is a row, and each type of observational unit forms a table.

> You can read more about the tidy data format in the [official `tidyr` vignette](https://cran.r-project.org/web/packages/tidyr/vignettes/tidy-data.html).

In [ ]:
(def train-df-long
 (-> train-df
  (stage-expand-time-features :datetime)
  (tc/select-columns [:demand-mw
                      :day-of-week
                      :hour-of-day
                      :minute-of-day
                      :weekend
                      :am
                      :day-of-month])
  (tc/pivot->longer
   (complement #{:demand-mw}) {:target-columns :feature
                               :value-column-name :value})))

#'user/train-df-long

In [ ]:
(-> train-df-long
 (tc/head 5))

forecast/taylor [5 3]: :demand-mw :feature :value 22262 :day-of-week MONDAY 21756 :day-of-week MONDAY 22247 :day-of-week MONDAY 22759 :day-of-week MONDAY 22549 :day-of-week MONDAY

Now that we’ve reshaped the data into a tidy format, we can explore how each of our engineered features relates to electricity demand. The plot below shows boxplots of `:demand-mw` grouped by different feature values. This is a one way to visually assess whether a feature might be informative for modeling.

So, let’s break all that stuff down:

- **AM vs PM (`:am`)**: Demand tends to be higher in the afternoon (`AM = 0`), with more variation compared to the morning hours.

- **Day of the Month (`:day-of-month`)**: No strong trend jumps out here — demand appears relatively stable across the month. This suggests that the day of the month may not be a particularly useful predictor on its own.

- **Day of the Week (`:day-of-week`)**: Here we see clear differences. Weekdays show higher and more variable demand, while weekends (especially Sunday) tend to have lower and more consistent demand. This is a strong sign that this feature could be useful for forecasting.

- **Minute of the Day (`:minute-of-day`)**: This feature captures the daily demand cycle beautifully. There’s a consistent rise in demand starting early in the morning, peaking between roughly 8 AM and early afternoon, and then gradually declining. This cyclical pattern makes it a very promising feature for time series modeling.

- **Weekend (`:weekend`)**: Similar to `:day-of-week`, this binary feature also shows a clear separation. Demand on weekends is generally lower and more stable, while weekdays show higher variation. It's a simple but highly informative feature.

These visual patterns indicate that our engineered features are meaningful and could help the model capture the structure of the data more effectively.

Next, we’ll move on to preparing the data for training and building our forecasting model.


In [ ]:
(-> {:data {:values (tc/rows train-df-long :as-maps)
            :format {:type "json"}}
     :spec {:layer [{:encoding {:y {:field "demand-mw" :type "quantitative"}
                                :x {:field "value" :type "nominal"}}
                     :mark {:type "boxplot"
                            :tooltip true}
                     :height 200
                     :width 800
                     :background "lightgrey"}
                    {:encoding {:y {:field "demand-mw" :type "quantitative"}
                                :x {:field "value" :type "nominal"}}
                     :mark {:type "point" :tooltip true
                            :color "red"
                            :fill "red"}
                     :transform  [{:aggregate [{
                                   :op "mean"
                                   :field "demand-mw" :as "demand-mw"
                                   }]
                                   :groupby ["value"]
                                  }]}]
         }
     :facet {:row {:field "feature"}}
     :resolve {:scale {:x "independent"}}}
  (show))

Embedding Vega-Lite

## Machine Learning Pipeline

As we move toward training and validating our model, it’s important to keep our workflow clean, reproducible, and easy to manage. That’s where machine learning pipelines come in.

In machine learning, we usually split our workflow into two main steps: preprocessing and modeling.

Preprocessing handles things like cleaning the data, dimensionality reduction, scaling values, extracting time-based patterns, etc. Then comes the modeling step, where we fit a learning algorithm to the preprocessed data.

Packing both of these steps into a single pipeline has a few big advantages. For one, it lets us treat the whole thing — data prep and modeling — as a single unit. That means we can train and evaluate everything together, and even tune hyperparameters in both parts. For example, we could search over the number of lag features to include, how many PCA components to keep, which imputation strategy to use, or even which model to run at the end. It also helps prevent common mistakes, like applying different logic to train and test data by accident.

In this tutorial, we are only tuning hyperparameters in the modeling step and keeping the preprocessing fixed for now, just to keep things simple. That said, the pipeline structure we’re using fully supports tuning preprocessing too, so it’s easy to expand into that later if needed.

So in short: pipelines help keep your ML process clean,consistent, and easy to deploy.

## Building a Preprocessing Pipeline

Now let’s put together a preprocessing pipeline that prepares our dataset for modeling. This includes selecting relevant columns, extracting features, encoding categorical variables, and normalizing numerical ones.

Here’s what the pipeline looks like:

In [ ]:
(defn mm-stage-expand-time-features [datetime-col]
 (mc/lift stage-expand-time-features datetime-col))

#'user/mm-stage-expand-time-features

In [ ]:
(def pipe-preprop
  (mc/pipeline
   (tc-mm/select-columns [:demand-mw :datetime])
   (ds-mm/set-inference-target :demand-mw)
   (mm-stage-expand-time-features :datetime)
   (ds-mm/categorical->one-hot [:minute-of-day :day-of-week])
   (mm-preprop/std-scale [:epoch-ms] {:mean? true :stddev? true})
   (ds-mm/drop-columns [:datetime :month :day-of-month])))

#'user/pipe-preprop

Ok, there's a lot of stuff happening above, let’s break it down

- **`select-columns`**  
  We start by keeping only the `:demand-mw` (our target variable) and `:datetime`, which we’ll use to extract time-based features.

- **`set-inference-target`**  
  This tells the pipeline which column we're trying to predict, in this case, `:demand-mw`.

- **`mm-stage-expand-time-features`**  
  This wraps our custom feature engineering function (`stage-expand-time-features`) and integrates it into the pipeline using `mc/lift`, so it plays nicely with the model workflow.

- **`categorical->one-hot`**  
  We convert `:minute-of-day` and `:day-of-week` into one-hot encoded vectors. This is a common technique used to represent categorical variables numerically so that machine learning models can understand them properly.

  **Why do we need this?**  
  Most models expect numerical input, and they don’t inherently understand that, for example, `:day-of-week = 1` means "Monday" and `= 5` means "Friday". If we left it as-is, the model might assume there's a numeric relationship between the days like "Friday is five times Monday" which clearly makes no sense.

  One-hot encoding solves this by creating a new binary column for each possible category. For example, say we have a `:day-of-week` value of 3 (Wednesday). The one-hot version would look like this:

  ```lisp
  [0 0 0 1 0 0 0]
  ```

  Only the column corresponding to the current value is set to `1`; all others are `0`.

  We apply the same transformation to `:minute-of-day`, which has many more possible values (0 to 1439). This can result in a large number of columns, so depending on the model, we may later choose to bucket or embed these instead but for now, one-hot encoding gives us a clean and model-friendly format where each time category is treated independently.

- **`std-scale`**  
  Here we normalize the `:epoch-ms` feature (a proxy for time/trend) using standard scaling subtracting the mean and dividing by the standard deviation. Crucially, this operation also returns the mean and standard deviation as context, so we can reuse them when processing the test set.
  > Why do this? Some models, especially linear ones, work better when features are centered around zero and have similar scales. Normalizing the data makes optimization more stable and helps the model learn faster and more accurately. Without this step, features with large numeric ranges (like timestamps) can dominate the learning process or lead to numerical issues.

- **`drop-columns`**  
  Finally, we remove any columns we no longer need for modeling, such as the raw `:datetime`, `:month`, or `:day-of-month` values.

This pipeline is modular, and thus easy to reason about, and returns both the transformed data and any relevant context. That makes it simple to apply the exact same steps to the test set later avoiding accidental data leakage.

In the next step, we’ll apply this pipeline to the training data and inspect the result.

In [ ]:
(def pipe-preprop-fitted-ctx
 (pipe-preprop {:metamorph/data train-df
                :metamorph/mode :fit}))

#'user/pipe-preprop-fitted-ctx

Let's inpsect the context:

In [ ]:
pipe-preprop-fitted-ctx

:metamorph/data forecast/taylor [3695 59]: :demand-mw :weekend :am :epoch-ms :minute-of-day-0.0 :minute-of-day-90.0 :minute-of-day-180.0 :minute-of-day-360.0 :minute-of-day-720.0 :minute-of-day-30.0 :minute-of-day-60.0 :minute-of-day-120.0 :minute-of-day-240.0 :minute-of-day-480.0 :minute-of-day-960.0 :minute-of-day-1410.0 :minute-of-day-690.0 :minute-of-day-1380.0 :minute-of-day-930.0 :minute-of-day-1350.0 :minute-of-day-330.0 :minute-of-day-660.0 :minute-of-day-1320.0 :minute-of-day-450.0 :minute-of-day-900.0 :minute-of-day-1290.0 :minute-of-day-630.0 :minute-of-day-1260.0 :minute-of-day-870.0 :minute-of-day-1230.0 :minute-of-day-150.0 :minute-of-day-300.0 :minute-of-day-600.0 :minute-of-day-1200.0 :minute-of-day-210.0 :minute-of-day-420.0 :minute-of-day-840.0 :minute-of-day-1170.0 :minute-of-day-570.0 :minute-of-day-1140.0 :minute-of-day-810.0 :minute-of-day-1110.0 :minute-of-day-270.0 :minute-of-day-540.0 :minute-of-day-1080.0 :minute-of-day-390.0 :minute-of-day-780.0 :minute-of-day-510.0 :minute-of-day-1020.0 :minute-of-day-1050.0 :minute-of-day-750.0 :minute-of-day-990.0 :day-of-week-MONDAY :day-of-week-TUESDAY :day-of-week-FRIDAY :day-of-week-SATURDAY :day-of-week-THURSDAY :day-of-week-SUNDAY :day-of-week-WEDNESDAY 22262 0 1 -1.73134779 1 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 1 0 0 0 0 0 0 21756 0 1 -1.73041040 0 0 0 0 0 1 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 1 0 0 0 0 0 0 22247 0 1 -1.72947302 0 0 0 0 0 0 1 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 1 0 0 0 0 0 0 22759 0 1 -1.72853563 0 1 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 1 0 0 0 0 0 0 22549 0 1 -1.72759825 0 0 0 0 0 0 0 1 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 1 0 0 0 0 0 0 22313 0 1 -1.72666087 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 1 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 1 0 0 0 0 0 0 22128 0 1 -1.72572348 0 0 1 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 1 0 0 0 0 0 0 21860 0 1 -1.72478610 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 1 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 1 0 0 0 0 0 0 21751 0 1 -1.72384872 0 0 0 0 0 0 0 0 1 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 1 0 0 0 0 0 0 21336 0 1 -1.72291133 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 1 0 0 0 0 0 0 0 0 0 1 0 0 0 0 0 0 ... ... ... ... ... ... ... ... ... ... ... ... ... ... ... ... ... ... ... ... ... ... ... ... ... ... ... ... ... ... ... ... ... ... ... ... ... ... ... ... ... ... ... ... ... ... ... ... ... ... ... ... ... ... ... ... ... ... ... 27771 1 0 1.72197395 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 1 0 0 0 0 0 0 0 0 0 0 0 0 1 0 27772 1 0 1.72291133 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 1 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 1 0 27625 1 0 1.72384872 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 1 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 1 0 27497 1 0 1.72478610 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 1 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 1 0 28461 1 0 1.72572348 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 1 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 1 0 29738 1 0 1.72666087 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 1 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 1 0 30108 1 0 1.72759825 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 1 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 1 0 29309 1 0 1.72853563 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 1 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 1 0 28351 1 0 1.72947302 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 1 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 1 0 26974 1 0 1.73041040 0 

### Understanding the Pipeline Output

After applying the pipeline to the training data, we get back two key things:

- **The transformed dataset** — in this case, `:metamorph/data`, which now includes all the processed features like one-hot encoded columns and the normalized `:epoch-ms`.

- **The context**, which captures everything the pipeline learned from the training data. This includes:
  - The mode the pipeline ran in (`:metamorph/mode` → `:fit`)
  - The mean and standard deviation used to normalize `:epoch-ms`
  - The internal ID of the pipeline run
  - Any intermediate transformation state needed for applying the same steps to the test data

The context tells us that when normalizing `:epoch-ms`, the pipeline subtracted a mean of approximately `9.63e11` and divided by a standard deviation of about `1.92e9`.

We’ll use this exact same context to transform the test set later on ensuring that the test data is preprocessed in the exact same way as the training data. This is essential for avoiding data leakage and making sure your evaluation is fair and accurate.

Let's apply the pipeline with the above context to the training set for inspection.

In [ ]:
(pipe-preprop (merge pipe-preprop-fitted-ctx
                {:metamorph/data train-df
                 :metamorph/mode :transform}))

:metamorph/data forecast/taylor [3695 59]: :demand-mw :weekend :am :epoch-ms :minute-of-day-0.0 :minute-of-day-90.0 :minute-of-day-180.0 :minute-of-day-360.0 :minute-of-day-720.0 :minute-of-day-30.0 :minute-of-day-60.0 :minute-of-day-120.0 :minute-of-day-240.0 :minute-of-day-480.0 :minute-of-day-960.0 :minute-of-day-1410.0 :minute-of-day-690.0 :minute-of-day-1380.0 :minute-of-day-930.0 :minute-of-day-1350.0 :minute-of-day-330.0 :minute-of-day-660.0 :minute-of-day-1320.0 :minute-of-day-450.0 :minute-of-day-900.0 :minute-of-day-1290.0 :minute-of-day-630.0 :minute-of-day-1260.0 :minute-of-day-870.0 :minute-of-day-1230.0 :minute-of-day-150.0 :minute-of-day-300.0 :minute-of-day-600.0 :minute-of-day-1200.0 :minute-of-day-210.0 :minute-of-day-420.0 :minute-of-day-840.0 :minute-of-day-1170.0 :minute-of-day-570.0 :minute-of-day-1140.0 :minute-of-day-810.0 :minute-of-day-1110.0 :minute-of-day-270.0 :minute-of-day-540.0 :minute-of-day-1080.0 :minute-of-day-390.0 :minute-of-day-780.0 :minute-of-day-510.0 :minute-of-day-1020.0 :minute-of-day-1050.0 :minute-of-day-750.0 :minute-of-day-990.0 :day-of-week-MONDAY :day-of-week-TUESDAY :day-of-week-FRIDAY :day-of-week-SATURDAY :day-of-week-THURSDAY :day-of-week-SUNDAY :day-of-week-WEDNESDAY 22262 0 1 -1.73134779 1 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 1 0 0 0 0 0 0 21756 0 1 -1.73041040 0 0 0 0 0 1 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 1 0 0 0 0 0 0 22247 0 1 -1.72947302 0 0 0 0 0 0 1 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 1 0 0 0 0 0 0 22759 0 1 -1.72853563 0 1 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 1 0 0 0 0 0 0 22549 0 1 -1.72759825 0 0 0 0 0 0 0 1 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 1 0 0 0 0 0 0 22313 0 1 -1.72666087 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 1 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 1 0 0 0 0 0 0 22128 0 1 -1.72572348 0 0 1 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 1 0 0 0 0 0 0 21860 0 1 -1.72478610 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 1 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 1 0 0 0 0 0 0 21751 0 1 -1.72384872 0 0 0 0 0 0 0 0 1 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 1 0 0 0 0 0 0 21336 0 1 -1.72291133 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 1 0 0 0 0 0 0 0 0 0 1 0 0 0 0 0 0 ... ... ... ... ... ... ... ... ... ... ... ... ... ... ... ... ... ... ... ... ... ... ... ... ... ... ... ... ... ... ... ... ... ... ... ... ... ... ... ... ... ... ... ... ... ... ... ... ... ... ... ... ... ... ... ... ... ... ... 27771 1 0 1.72197395 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 1 0 0 0 0 0 0 0 0 0 0 0 0 1 0 27772 1 0 1.72291133 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 1 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 1 0 27625 1 0 1.72384872 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 1 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 1 0 27497 1 0 1.72478610 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 1 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 1 0 28461 1 0 1.72572348 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 1 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 1 0 29738 1 0 1.72666087 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 1 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 1 0 30108 1 0 1.72759825 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 1 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 1 0 29309 1 0 1.72853563 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 1 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 1 0 28351 1 0 1.72947302 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 1 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 1 0 26974 1 0 1.73041040 0 

The preprocessing pipeline creates 58 features.

In [ ]:
(-> pipe-preprop-fitted-ctx
 :metamorph/data
 tc/shape)

3695 59

## Modeling

With our preprocessing pipeline in place, we're now ready to move on to the modeling stage of the pipeline.

The goal here is to train a machine learning model that can learn patterns from the data and make accurate predictions on future electricity demand.

### Ridge Regression: Regularized Linear Modeling

To start, we’ll use **Ridge Regression** which is a regularized version of linear regression that includes **L2 penalty** on the model’s coefficients. This helps prevent overfitting, especially when dealing with a large number of features, some of which might not be very informative (like a ton of time-of-day dummy variables from one-hot encoding).

The strength of this regularization is controlled by a parameter called `λ` (lambda):

- A **small lambda** behaves like regular linear regression — all features are used freely.
- A **large lambda** penalizes large coefficients more strongly, automatically shrinking the weights of less useful features.

This is especially helpful in our case because we don't know ahead of time which time-based features are truly predictive. Ridge regression can downweight the irrelevant ones without removing them entirely.

One important detail is that lambda is a hyperparameter, meaning it's not something the model learns during training. Instead, it must be chosen before training starts.

Why? Because lambda is baked into the cost function that Ridge regression minimizes. The model needs to know how much to penalize the weights before it can start learning. So, we can't learn lambda and the coefficients at the same time we need to pick lambda first.

### Cross-Validation to the Rescue

To choose the best lambda, we use a technique called cross-validation. It works like this:

- Split the training data into several folds.
- For each candidate lambda, train a model on some folds and evaluate it on the others.
- Average the performance across folds.
- Select the lambda that performs best overall.

This gives us a solid estimate of how well each lambda generalizes to unseen data — without ever touching the test set.

> For more details on Ridge Regression and cross-validation, check out The Elements of Statistical Learning by Hastie, Tibshirani, and Friedman, IMHO, one of the best resources in the field.

### Generating a Grid of Lambda Values

Instead of just guessing, we create a range of possible lambda values for the model to try by sampling from a log-normal distribution.

In our case, we’re going to sample 50 values. You can sample as many as you want but just keep in mind that the more values you try, the more models you’ll have to train, and that can get pretty expensive computationally.

There are more efficient strategies out there, like Bayesian optimization, which can help you find good hyperparameters with fewer evaluations, but I won’t go into that in this tutorial.

In [ ]:
(def lambda-grid
 (->> (r/->seq (r/distribution :log-normal {:scale 2.0 :shape 2.5}) 50)))

#'user/lambda-grid

### Why Sample Lambda from a Log-Normal Distribution?

When tuning the `λ` (lambda) hyperparameter in Ridge Regression, we want to explore a wide range of values — often across several orders of magnitude. A simple linear scale (e.g., `0.1`, `0.2`, `0.3`, ...) won't be suitable.

Instead, we sample from a log-normal distribution, and here's why:

- **Covers a wide dynamic range**: Log-normal values span from very small to very large, allowing us to explore both weak and strong regularization settings.
- **More density at lower values**: Often, the best lambda is small but not too small. Log-normal sampling gives us better resolution in that sweet spot.
- **Avoids arbitrary spacing**: Unlike manually-defined grids, log-normal sampling gives a more natural, randomized spread of values.

### Visualizing the Lambda Distribution

To better understand what our lambda grid looks like, here’s a plot of the values we sampled from the log-normal distribution:

As you can see, the distribution is right-skewed, with a concentration of smaller lambda values and a long tail reaching into larger values. This is exactly what we want:

- It gives us finer resolution in the lower range where the best lambda often lies (it's an assumption of course).
- At the same time, it still lets us explore larger regularization strengths just in case our model benefits from stronger weight penalties.
- Compared to a linear or evenly spaced grid, this approach avoids arbitrary gaps and gives us a more natural coverage of the hyperparameter space.

This makes log-normal sampling a good choice when tuning regularization parameters like `λ`, especially when you're unsure of the scale ahead of time.

In [ ]:
(-> (tc/dataset {:lambda lambda-grid})
  (hanami/base {:=x :lambda})
  (hanami/layer-histogram)
  (assoc :background "lightgrey"
         :width 500
         :height 300)
  (hanami/plot)
  show)

Embedding Vega-Lite

### Generating a Model Spec for Each Lambda

Now that we’ve sampled a range of lambda values from a log-normal distribution, we need to create a separate model configuration (or "spec") for each one. This is important because each lambda represents a different setting for the Ridge Regression model and we want to evaluate them individually through cross-validation.

Here’s how we generate the list of lambda hyperparameter maps:

In [ ]:
(def hyperparam-specs
 (->> lambda-grid
  (map (fn [x] {:lambda x}))))

(take 3 hyperparam-specs)

:lambda 1.1129235094939267 :lambda 636.0784123715174 :lambda 4.9001313942554

Each of these maps represents one configuration, a different strength of regularization we want to try out.

Next, we attach the model type to each config, specifying that we want to use Ridge Regression for all of them:

In [ ]:
(def ridge-regression-specs
  (map
   #(assoc % :model-type :smile.regression/ridge)
   hyperparam-specs))

(take 3 ridge-regression-specs)

:lambda 1.1129235094939267 :model-type :smile.regression/ridge :lambda 636.0784123715174 :model-type :smile.regression/ridge :lambda 4.9001313942554 :model-type :smile.regression/ridge

We now have a collection of model specifications we can use in our ml pipiline.

### Assembling Full Pipelines for Cross-Validation

Now that we’ve created a set of Ridge Regression model specifications with different `λ` values, the next step is to combine each one with our preprocessing pipeline.

That way, we can evaluate the entire pipeline from raw features to final predictions under cross-validation, with each pipeline using a different value of `λ`.

To do this, we define a helper function that combines the preprocessing and modeling steps into a full pipeline:

In [ ]:
(defn make-pipe
 [preprop-spec model-spec]
 (mc/pipeline
  preprop-spec
  {:metamorph/id :model}
  (ml/model model-spec)))

#'user/make-pipe

Then we generate one pipeline per model spec:

In [ ]:
(def pipe-fns
 (for [spec ridge-regression-specs]
  (make-pipe pipe-preprop spec)))

#'user/pipe-fns

This gives us a list of full pipelines each with:

The same preprocessing logic (feature engineering, normalization, one-hot encoding, etc.). A different Ridge Regression model using a unique λ value. Finally, each of these pipelines can now be evaluated independently in cross-validation, making it easy to find the λ that gives the best overall performance.

### Rolling-Origin Cross-Validation for Time Series

Unlike standard cross-validation (which randomly shuffles and splits data), time series forecasting requires us to respect the order of time. We can’t train on future data and validate on the past, that would introduce data leakage and give us overly optimistic results.

To handle this, we use rolling-origin cross-validation. This technique simulates a real-world scenario where:

- You train your model on all available data up to a certain point in time
- Then make predictions for the next `horizon` steps
- Then roll the training window backward and repeat the process

This gives you multiple evaluations across different historical periods, all respecting time order.

Here’s how we implement it in Clojure:

In [ ]:
(defn rolling-origin-cv
  [df num-splits horizon]
  (let [n (tc/row-count df)]
    (loop [splits []
           start (- n horizon)
           split-count 0]
      (if (or (< start (/ horizon 2)) (>= split-count num-splits))
        splits
        (let [train-df (tc/select-rows df (range start))
              test-df (tc/select-rows df (range start (+ start horizon)))]
          (recur (conj splits {:train train-df :test test-df})
                 (- start horizon)
                 (inc split-count)))))))

#'user/rolling-origin-cv

Now let's create 5 CV folds:

In [ ]:
(def train-test-splits
 (rolling-origin-cv train-df 5 (* forecast-horizon 24 2))) ;; The horizon of 7 days is 336 half-hour data points

#'user/train-test-splits

### Visualizing Rolling-Origin Cross-Validation

To better understand how rolling-origin cross-validation works, let’s visualize the splits over time.

Following the tidy data principle, we’ll add two columns to each row in the split data:

- `:fold` — the fold number
- `:set` — either `"train"` or `"test"`

This turns the collection of train/test splits into a single, long-format dataset that’s perfect for plotting.

The end result will look something like this:

In [ ]:
(defn combine-cv-splits
  [splits]
  (let [split-dfs (map-indexed
                    (fn [idx {:keys [train test]}]
                      (let [train-labeled (tc/add-columns train {:fold (str "fold-" idx) :set "train"})
                            test-labeled  (tc/add-columns test {:fold (str "fold-" idx) :set "test"})]
                        (tc/concat train-labeled test-labeled)))
                    splits)]
    (apply tc/concat split-dfs)))

#'user/combine-cv-splits

In [ ]:
(def train-test-splits-df
 (combine-cv-splits train-test-splits))

#'user/train-test-splits-df

In [ ]:
(tc/head train-test-splits-df)

forecast/taylor [5 6]: :rownames :demand-mw :datetime :is-train :fold :set 1 22262 2000-06-05T00:00 1 fold-0 train 2 21756 2000-06-05T00:30 1 fold-0 train 3 22247 2000-06-05T01:00 1 fold-0 train 4 22759 2000-06-05T01:30 1 fold-0 train 5 22549 2000-06-05T02:00 1 fold-0 train

Now that we’ve reshaped our rolling-origin cross-validation splits into a tidy format, we can visualize how each fold separates training and testing data over time.

In the plot below:

- Each **row** represents one CV fold.
- The **orange line** shows the training data for that fold.
- The **blue line** shows the test set (the forecast horizon).
- The x-axis is time (`:datetime`), and the y-axis is electricity demand (`:demand-mw`).

As you can see, the test window (blue) moves backward in time with each fold, while the training window stretches all the way up to the start of the test set. This simulates a real-world forecasting workflow, where you train on past data and predict a future window.

Next, we’ll use these splits to evaluate our full pipelines and select the best-performing model configuration.

In [ ]:
(-> {:data {:values (tc/rows train-test-splits-df :as-maps)
            :format {:type "json"}}
     :spec {:layer [{:encoding {:y {:field "demand-mw" :type "quantitative"}
                                :x {:field "datetime" :type "temporal"}
                                :color {:field "set" :type "nominal"}}
                     :mark {:type "line"
                            :tooltip true}
                     :height 200
                     :width 800
                     :background "lightgrey"}]}
     :facet {:row {:field "fold" :type "nominal"}}}
  (show))

Embedding Vega-Lite

### There's Still One Ingredient That's Missing — Performance Metric

Before we can evaluate our models and pick the best one, we need to decide **how** we're measuring performance. In other words, what's our error function?

In this case, we're using **Root Mean Squared Error (RMSE)** — a standard metric for regression tasks. It tells us how far off our predictions are from the actual values, while penalizing larger errors more heavily.

Here’s its definition:

$$
\text{RMSE} = \sqrt{ \frac{1}{n} \sum_{i=1}^{n} (\hat{y}_i - y_i)^2 }
$$

Where:

- `ŷᵢ` is the predicted value  
- `yᵢ` is the actual (true) value  
- `n` is the number of predictions (7 days of half-hourly data in our case)


This gives us a single number that summarizes the average error, in our case, in megawatts. Since errors are squared before being averaged, bigger mistakes have more impact on the final score.

### Why RMSE?

- It’s sensitive to large errors, which makes sense in our context as big forecast misses are more costly.
- It’s interpretable - lower is better, and it's in the same units as our target variable.

Now that we’ve locked in RMSE as our evaluation metric, we can move on to running cross-validation across all our pipelines.

## Evaluating Models

Below is the code that trains each pipeline on the training set, makes a forecast over the 7-day horizon, and then computes the RMSE for each fold from the rolling-origin cross-validation we plotted earlier.

It takes some time to train and evaluate all the pipelines.

In [ ]:
(def evaluation-results-all
  (ml/evaluate-pipelines
   pipe-fns
   train-test-splits
   loss/rmse
   :loss
   {:map-fn :map
    :return-best-crossvalidation-only false
    :return-best-pipeline-only false}))

#'user/evaluation-results-all

In [ ]:
(count evaluation-results-all)

50

Now that we’ve run all our pipelines through rolling-origin cross-validation, we need to combine the results into a single dataset so we can plot and analyze them.

The following code extracts the `:lambda` used by each model and the corresponding average RMSE, and turns it into a tidy dataset:

In [ ]:
(defn make-results-ds
 [evaluation-results]
  (->> evaluation-results
       flatten
       (map #(hash-map :options (-> % :test-transform :ctx :model :options)
                       :rmse (-> % :test-transform :mean)))
       tc/dataset))

(def perfs
 (-> (make-results-ds evaluation-results-all)
  (tc/unique-by)
  (tc/order-by [:rmse] :desc)
  (tc/map-columns :lambda [:options] #(:lambda %))))

#'user/perfs

### Cross-Validation Performance vs. Lambda

The plot below shows the average RMSE across all CV folds for each value of `λ`:

We can clearly see the effect of regularization:

- When `λ` is close to zero, the model behaves more like standard linear regression, it fits the data more freely.
- As `λ` increases, regularization gets stronger, and the model starts to shrink coefficients, simplifying its behavior.
- Up to a point, this helps reduce overfitting, but after that, too much regularization starts to underfit, and RMSE increases.

That said, the dip in RMSE isn’t very sharp as the curve is fairly flat around the minimum. This suggests that the model isn't extremely sensitive to the exact value of lambda given our data, at least within a reasonable range. Still, we can see a clear trend: too little or too much regularization both lead to worse performance.

We'll go with the `λ` value that gives us the lowest RMSE and use that pipeline as our final model.

In [ ]:
(-> perfs
  (hanami/base {:=x :lambda
                :=y :rmse})
  (hanami/layer-line)
  (assoc :background "lightgrey"
         :width 500
         :height 300)
  (hanami/plot)
  show)

Embedding Vega-Lite

To get the best lambda, we just grab the top row from the sorted performance dataset:

In [ ]:
(def best-lambda
 (-> perfs
    (tc/order-by [:rmse] :asc)
    tc/first
    :lambda
    first))

best-lambda

138.8923440772294

Now that we’ve selected the best `λ` from cross-validation, we can build our final pipeline by plugging that value into the model.

We first define a new ML kernel with the chosen lambda:

In [ ]:
(def best-ml-kernel
 (mc/pipeline
  {:metamorph/id :model}
  (ml/model {:model-type :smile.regression/ridge
             :lambda best-lambda})))

#'user/best-ml-kernel

Then we combine it with the same preprocessing pipeline we’ve been using all along:

In [ ]:
(def best-pipe
 (mc/pipeline
  pipe-preprop
  best-ml-kernel))

#'user/best-pipe

Finally, we fit the entire pipeline on the full training data:

In [ ]:
(def best-pipe-fitted-ctx
 (best-pipe {:metamorph/data train-df
             :metamorph/mode :fit}))

#'user/best-pipe-fitted-ctx

## Test Set Perf Evaluation

You remember we set aside a test set earlier the one covering the final 7 days of the dataset?  
Now that we’ve trained our final pipeline using the best lambda from cross-validation, we can use that test set to evaluate how well the model performs on completely unseen data.

This step gives us a reasonable estimate of real-world performance but let’s be clear: it’s not a perfect or fully "honest" evaluation.

Why?

- The test set still comes from the same distribution as the training data.
- The result is still conditioned on the specific training period we trained the model on.
- In the real world, things can change as demand patterns shift, holidays pop up, new behavior emerges (aka data drift).

That said, setting aside a hold-out test set is still best practice. It’s the cleanest offline estimate we can get, and it protects us from overfitting to the cross-validation folds during hyperparameter tuning.

In [ ]:
(def forecast
  (best-pipe
   (merge best-pipe-fitted-ctx
          {:metamorph/data test-df
           :metamorph/mode :transform})))

#'user/forecast

In [ ]:
(def forecast-ts
 (-> forecast
  :metamorph/data
  :demand-mw))

#'user/forecast-ts

## Visualizing Out-of-Sample Forecast Performance

Now that we’ve generated forecasts on the hold-out test set using our final pipeline, let’s dig into how the model actually performed visually.

### Actual vs. Predicted Time Series

In this plot:

- The blue line is the actual electricity demand (`:demand-mw`)
- The red line is our model’s predicted demand (`:demand-mw-pred`)

We can see that the model captures the overall structure quite well, the daily cycles, peak shapes, and general magnitude. It’s not perfect (we'll look at that next), but it tracks reality reasonably well across the full 7-day horizon.

In [ ]:
(-> test-df
  (tc/add-column :demand-mw-pred forecast-ts)
  (hanami/base {:=x :datetime
                :=y :demand-mw})
  (hanami/layer-line)
  (hanami/layer-line {:=x :datetime
                      :=y :demand-mw-pred
                      :=mark-color "red"})
  (assoc :background "lightgrey"
         :width 900
         :height 300)
  (hanami/plot)
  show)

Embedding Vega-Lite

### Predicted vs. Actual Scatter Plot

This scatter plot compares predicted values (x-axis) to actual values (y-axis), with a red line showing the ideal match.

- The points generally hug the line, especially in the mid-to-high range.
- The spread increases a bit in lower-demand areas, suggesting more variance when demand is low.
- Overall, this confirms that the model is more or less calibrated
- It's clear though, that there exists some pattern between the actual and predicted values.

In [ ]:
(-> test-df
  (tc/add-column :demand-mw-pred forecast-ts)
  (hanami/base {:=x :demand-mw-pred
                :=y :demand-mw})
  (hanami/layer-point)
  (hanami/layer-smooth {:=mark-color "red"})
  (assoc :background "lightgrey"
         :width 600
         :height 600)
  (hanami/plot)
  show)

Embedding Vega-Lite

### Residuals Histogram

Residuals are just the difference between the actual and predicted values:

$$
residual = actual - predicted
$$

Most residuals fall between 0 and 2000 MW, but there's a slight skew, that is more cases where the model underestimates demand than overestimates.

In [ ]:
(-> test-df
  (tc/add-column :demand-mw-pred forecast-ts)
  (tc/- :resid [:demand-mw :demand-mw-pred])
  (hanami/base {:=x :resid})
  (hanami/layer-histogram)
  (assoc :background "lightgrey"
         :width 500
         :height 300)
  (hanami/plot)
  show)

Embedding Vega-Lite

### Residuals Over Time

Finally, this plot shows how the residuals change over time:

- There’s some clear structure here, spikes around the same time each day.
- That might indicate systematic underprediction during peak hours, especially near the start and end of the test period.
- There’s also a noticeable increase in error variance toward the end, which might hint at a bit of concept drift or just some higher variability during those days.
- It’s also clear that there’s some autocorrelation left in the residuals, although I won’t be computing or analyzing it in this tutorial. But in short, it’s possible to use that structure to improve forecasts.

In [ ]:
(-> test-df
  (tc/add-column :demand-mw-pred forecast-ts)
  (tc/- :resid [:demand-mw :demand-mw-pred])
  (hanami/base {:=x :datetime :=y :resid})
  (hanami/layer-line)
  (assoc :background "lightgrey"
         :width 800
         :height 300)
  (hanami/plot)
  show)

Embedding Vega-Lite

### Overall

The model performs reasonably well, with:

- Good alignment with daily demand cycles
- Low and relatively stable RMSE
- Mostly well-distributed residuals

But there's still room to improve, particularly around fine-tuning peak demand predictions and reducing that slight bias. That’s the kind of insight you only get from digging into the visuals and residuals, not just a single metric.


## Generating and Visualizing a 7-Day Forecast

Now that we’ve evaluated our model's performance on holdout data, it's time to shift gears and generate a true out-of-sample forecast, one that reaches into the future, beyond the range of our historical data.

We start by constructing a time grid that covers the next 7 days in half-hour increments:

In [ ]:
(def forecast-horizon-steps (* 7 48)) ;; 7 days of half-hourly intervals

#'user/forecast-horizon-steps

That gives us 336 time steps — one for every 30-minute slot in a week.



Next, we generate the sequence of future timestamps, starting right after the last timestamp in our original data:

In [ ]:
(defn forecast-datetime-grid
  [last-datetime steps]
  (->> (iterate #(jtime/plus % (jtime/minutes 30)) last-datetime)
       rest
       (take steps)))

 (def forecast-grid (forecast-datetime-grid (last datetime-grid) forecast-horizon-steps))

#'user/forecast-grid

With our timestamps in hand, we build a new dataset, shaped exactly like the training data, but with :demand-mw set to nil. This is essential because Metamorph pipelines expect the same schema during prediction:

In [ ]:
(def forecast-df
  (tc/dataset {:datetime forecast-grid
               :demand-mw (repeat forecast-horizon-steps nil)}))

#'user/forecast-df

Then, we feed this into the trained pipeline in :transform mode to generate the actual forecast:

In [ ]:
(def final-forecast
  (best-pipe
   (merge best-pipe-fitted-ctx
          {:metamorph/data forecast-df
           :metamorph/mode :transform})))

(def final-forecast-output
  (-> final-forecast
      :metamorph/data
      (tc/add-column :datetime forecast-grid)))

#'user/final-forecast-output

In [ ]:
(tc/head final-forecast-output 3)

:_unnamed [3 2]: :demand-mw :datetime 24605.11149759 2000-08-28T00:00 23896.86784192 2000-08-28T00:30 23824.24263497 2000-08-28T01:00

We add a :ts-type column to label each row as either :historical or :forecast. This helps us distinguish them visually.

In [ ]:
(def combined-ts
 (tc/concat
  (-> ts-data
   (tc/select-columns [:demand-mw	:datetime])
   (tc/add-column :ts-type :historical))
  (-> final-forecast-output
   (tc/add-column :ts-type :forecast))))

#'user/combined-ts

Finally, we plot both the past and predicted demand on a common timeline using Hanami:

In [ ]:
(-> combined-ts
    (hanami/base {:=x :datetime
                  :=y :demand-mw})
    (hanami/layer-line {:=color "ts-type"})
    (assoc :background "lightgrey"
           :width 600
           :height 300)
    (hanami/plot)
    show)

Embedding Vega-Lite

## Wrapping Up

Alright, we’ve now walked through a full time series forecasting workflow in Clojure from building a half-hourly datetime grid, training a model, and generating a 7-day forecast, all the way to visualizing the results.

We used some nice tools from the Scicloj ecosystem, tablecloth for wrangling, metamorph.ml for the pipeline, and hanami for plotting. Everything fits together in a way that’s simple, composable, and actually kinda fun to work with.

If you’ve made it this far, you now have a pretty good forecasting (and predictive ML in general) setup you can build on. You can add more features, try different models, tune things further, or even plug in weather or holiday data if you're really into it.

# What’s next?

A few ideas to explore:

- Add lag features, to extract more signal by utilizing temporal dependence

- Model the residuals using ARIMA and then combine it with the ridge regression above.

- Test different learners (XGBoost, ElasticNet, etc.) and compare performance

- Add confidence intervals if you want to show forecast uncertainty

- Add more features like temperature, for example.

Thanks for following along, happy machine learning!